In [3]:
import sys
import os
import numpy as np
import nltk
from nltk.stem import PorterStemmer
from nltk.corpus import stopwords 
from nltk.tokenize import RegexpTokenizer, sent_tokenize, word_tokenize

train_data_size = 1000
test_data_size = 1000
DIC_SIZE = 10000
# nltk.download('stopwords')

In [130]:
# dic = buildVocabulary(os.getcwd()+'/aclImdb/train/')
# vocabulary = loadDic(os.getcwd()+'/aclImdb/imdb.vocab')
# Xtrain, Xtest, ytrain, ytest = loadData(os.getcwd()+'/aclImdb/', vocabulary) # BOW representations


array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 6],
       [0, 0, 0, ..., 0, 0, 5],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]])

In [55]:
vocabulary = loadDic(os.getcwd()+'/aclImdb/imdb.vocab')


# load tokens
Xtrain_tok, Xtest_tok, ytrain, ytest = loadData(os.getcwd()+'/aclImdb/', vocabulary)


# load pre-trained 50D word embedding
word_embedding = load_word_embedding('glove.6B/glove.6B.50d.txt')


# build sentence representations
trn_representations = construct_sentence_rep(trn_tokens, word_embedding)
dev_representations = construct_sentence_rep(dev_tokens, word_embedding)



[['for',
  'a',
  'movie',
  'that',
  'gets',
  'no',
  'respect',
  'there',
  'sure',
  'are',
  'a',
  'lot',
  'of',
  'memorable',
  'quotes',
  'listed',
  'for',
  'this',
  'gem',
  'imagine',
  'a',
  'movie',
  'where',
  'joe',
  'piscopo',
  'is',
  'actually',
  'funny',
  'maureen',
  'stapleton',
  'is',
  'a',
  'scene',
  'stealer',
  'the',
  'moroni',
  'character',
  'is',
  'an',
  'absolute',
  'scream',
  'watch',
  'for',
  'alan',
  'the',
  'skipper',
  'hale',
  'jr',
  'as',
  'a',
  'police',
  'sgt'],
 ['bizarre',
  'horror',
  'movie',
  'filled',
  'with',
  'famous',
  'faces',
  'but',
  'stolen',
  'by',
  'cristina',
  'raines',
  'later',
  'of',
  'tv',
  's',
  'flamingo',
  'road',
  'as',
  'a',
  'pretty',
  'but',
  'somewhat',
  'unstable',
  'model',
  'with',
  'a',
  'gummy',
  'smile',
  'who',
  'is',
  'slated',
  'to',
  'pay',
  'for',
  'her',
  'attempted',
  'suicides',
  'by',
  'guarding',
  'the',
  'gateway',
  'to',
  'hell',

In [54]:
def buildVocabulary(Path):
    tokenizer = RegexpTokenizer(r'\w+') #tokenizer removing puncturations
    ps = PorterStemmer()
    stop_words = set(stopwords.words('english')) 
    tokens = []
    for folder in os.listdir(Path):
        for filename in os.listdir(Path+folder):
            data = open(Path+folder+'/'+filename, 'r')
            raw = data.read()
            token = tokenizer.tokenize(raw)
            # stop words removal
            filtered_token = [w for w in token if not w in stop_words]
#             filtered_token = [ps.stem(w) for w in token if not w in stop_words]
            # stemming
            for i in range(len(filtered_token)):
                filtered_token[i] = ps.stem(filtered_token[i])
            tokens.extend(filtered_token)
    word_counts = Counter(tokens).most_common(3999)
    vocab = {}
    i = 0
    for word_count in word_counts:
        vocab[word_count[0]] = i
        i += 1
    vocab['UNK'] = i
    return vocab

def loadDic(Path, skip_stop = False, stem = False, lower = True):
    dic = open(Path,'r')
    dic = dic.read().split('\n')
    
    # stop words removal and stemming
    ps = PorterStemmer()
    stop_words = set(stopwords.words('english'))
    if stem:
        dic = list(set([ps.stem(w) for w in dic]))
    if skip_stop:
        dic = list(set([w for w in dic if not w in stop_words]))
    if lower:
        dic = list(set([w.lower() for w in dic]))
    else:
        dic = list(set(dic))
    
    
    # transfer to dictionary
    
    filtered_dic = {word: i for i, word in enumerate(dic)}
    filtered_dic['UNK'] = len(filtered_dic)
    return filtered_dic

# def loadData(Path, vocabulary):
#     voc_size = len(vocabulary)
#     Xtrain = np.zeros((train_data_size*2,voc_size), dtype=int)
#     Xtest = np.zeros((train_data_size*2,voc_size), dtype=int)
#     ytrain = np.concatenate((np.ones(train_data_size, dtype=int),np.zeros(train_data_size, dtype=int)), axis = 0)
#     ytest = np.concatenate((np.ones(train_data_size, dtype=int),np.zeros(train_data_size, dtype=int)), axis = 0)
    
#     for i, filename in enumerate(os.listdir(Path+'train/pos/')[:train_data_size]):
# #         Xtrain.append(transfer(Path+'train/pos/'+filename, vocabulary))
#         Xtrain[i] = transfer(Path+'train/pos/'+filename, vocabulary)

#     for i, filename in enumerate(os.listdir(Path+'train/neg/')[:train_data_size]):
#         Xtrain[i] = transfer(Path+'train/neg/'+filename, vocabulary)
# #         Xtrain.append(transfer(Path+'train/neg/'+filename, vocabulary))

#     for i, filename in enumerate(os.listdir(Path+'test/pos/')[:test_data_size]):
#         Xtest[i] = transfer(Path+'test/pos/'+filename, vocabulary)
# #         Xtest.append(transfer(Path+'test/pos/'+filename, vocabulary))

#     for i, filename in enumerate(os.listdir(Path+'test/neg/')[:test_data_size]):
#         Xtest[i] = transfer(Path+'test/neg/'+filename, vocabulary)
# #         Xtest.append(transfer(Path+'test/neg/'+filename, vocabulary))

# #     Xtrain, Xtest = np.array(Xtrain), np.array(Xtest)
#     return Xtrain, Xtest, ytrain, ytest


def loadData(Path, vocabulary):
    Xtrain = []
    Xtest = []
    ytrain = np.concatenate((np.ones(train_data_size, dtype=int),np.zeros(train_data_size, dtype=int)), axis = 0)
    ytest = np.concatenate((np.ones(train_data_size, dtype=int),np.zeros(train_data_size, dtype=int)), axis = 0)
    
    tokenizer = RegexpTokenizer(r'\w+') #tokenizer removing puncturations
    
    for i, filename in enumerate(os.listdir(Path+'train/pos/')[:train_data_size]):
        data = open(Path+'train/pos/'+filename,'r')
        raw = data.read().lower()
        tokens = tokenizer.tokenize(raw)
        Xtrain.append(tokens)

    for i, filename in enumerate(os.listdir(Path+'train/neg/')[:train_data_size]):
        data = open(Path+'train/neg/'+filename,'r')
        raw = data.read()
        tokens = tokenizer.tokenize(raw)
        Xtrain.append(tokens)

    for i, filename in enumerate(os.listdir(Path+'test/pos/')[:test_data_size]):
        data = open(Path+'test/pos/'+filename,'r')
        raw = data.read()
        tokens = tokenizer.tokenize(raw)
        Xtest.append(tokens)

    for i, filename in enumerate(os.listdir(Path+'test/neg/')[:test_data_size]):
        data = open(Path+'test/neg/'+filename,'r')
        raw = data.read()
        tokens = tokenizer.tokenize(raw)
        Xtest.append(tokens)
        
    return Xtrain, Xtest, ytrain, ytest


def transfer(fileDj, vocabulary):
    data = open(fileDj,'r')
    BOWDj = np.zeros((len(vocabulary),), dtype = int)
    
    tokenizer = RegexpTokenizer(r'\w+') #tokenizer removing puncturations
    ps = PorterStemmer()
    stop_words = set(stopwords.words('english')) 
    
    raw = data.read()
    tokens = tokenizer.tokenize(raw)
    # stop words removal
    filtered_token = [ps.stem(w) for w in tokens if not w in stop_words]
#     # stemming
#     for i in range(len(filtered_token)):
#         filtered_token[i] = ps.stem(filtered_token[i])
    # transfer to BOW
    for token in filtered_token:
        if token in vocabulary:
            BOWDj[vocabulary[token]] += 1
        else:
            BOWDj[vocabulary['UNK']] += 1
    
    return BOWDj


def token_to_index(tokens, vocabulary):
    lower_token = [w.lower() for w in tokens]
    return [vocabulary.get(token, None) for token in lower_token]


def loadWordIndex(Path, vocabulary):
    voc_size = len(vocabulary)
    Xtrain = []
    Xtest = []
    ytrain = np.concatenate((np.ones(train_data_size, dtype=int),np.zeros(train_data_size, dtype=int)), axis = 0)
    ytest = np.concatenate((np.ones(train_data_size, dtype=int),np.zeros(train_data_size, dtype=int)), axis = 0)
    
    tokenizer = RegexpTokenizer(r'\w+') #tokenizer removing puncturations
    ps = PorterStemmer()
    stop_words = set(stopwords.words('english')) 

    for i, filename in enumerate(os.listdir(Path+'train/pos/')[:train_data_size]):
        data = open(Path+'train/pos/'+filename,'r')
        raw = data.read()
        tokens = tokenizer.tokenize(raw)
        Xtrain.append(token_to_index(tokens, vocabulary))

    for i, filename in enumerate(os.listdir(Path+'train/neg/')[:train_data_size]):
        data = open(Path+'train/neg/'+filename,'r')
        raw = data.read()
        tokens = tokenizer.tokenize(raw)
        Xtrain.append(token_to_index(tokens, vocabulary))

    for i, filename in enumerate(os.listdir(Path+'test/pos/')[:test_data_size]):
        data = open(Path+'test/pos/'+filename,'r')
        raw = data.read()
        tokens = tokenizer.tokenize(raw)
        Xtest.append(token_to_index(tokens, vocabulary))

    for i, filename in enumerate(os.listdir(Path+'test/neg/')[:test_data_size]):
        data = open(Path+'test/neg/'+filename,'r')
        raw = data.read()
        tokens = tokenizer.tokenize(raw)
        Xtest.append(token_to_index(tokens, vocabulary))

    return Xtrain, Xtest, ytrain, ytest    


def load_word_embedding(Path):
    file = open(Path, 'r')
    embedding = {}
    for line in file:
        line = line.split()
        embedding[line[0]] = np.array(line[1:], dtype = float)
    return embedding


def construct_sentence_rep(data, word_embedding):
    sentence_reps = []
    for tokens in data:
        current_res = np.zeros((50,), dtype=float)
        for token in tokens:
            if token in word_embedding:
                current_res += word_embedding[token]
            else:
                current_res += word_embedding['unk']
        if len(tokens)==0: 
            current_res = word_embedding['unk']
        else:
            current_res /= len(tokens)
        sentence_reps.append(current_res)
    return np.array(sentence_reps, dtype=float)
